In [1]:
from bs4 import BeautifulSoup as bs 
import pandas as pd
import requests
from splinter import Browser
import json
from webdriver_manager.chrome import ChromeDriverManager
from sqlalchemy import create_engine
import numpy as np
import pymongo

In [2]:
# Scrape the [Tesla Deaths Site](https://www.tesladeaths.com/)
executable_path = {'executable_path': ChromeDriverManager().install()}
browser = Browser('chrome', **executable_path, headless=False)

[WDM] - ====== WebDriver manager ======
[WDM] - Current google-chrome version is 90.0.4430
[WDM] - Get LATEST driver version for 90.0.4430


[WDM] - Driver [C:\Users\pamhi\.wdm\drivers\chromedriver\win32\90.0.4430.24\chromedriver.exe] found in cache


In [3]:
url = 'https://www.tesladeaths.com/'
browser.visit(url)

In [4]:
# Collect the table headers and data.

# HTML object
html = browser.html
# Parse HTML with Beautiful Soup
soup = bs(html, 'html.parser')

In [5]:
tesla_facts_url = 'https://www.tesladeaths.com/'
tesla_table_read = pd.read_html(tesla_facts_url)
tesla_table_read

[    Unnamed: 0    Year  Unnamed: 2       Date Country State  \
 0          NaN  2021.0         NaN  17-Apr-21   China   NaN   
 1          NaN  2021.0         NaN  17-Apr-21     USA    TX   
 2          NaN  2021.0         NaN  16-Apr-21  France   NaN   
 3          NaN  2021.0         NaN  14-Apr-21     USA    TX   
 4          NaN  2021.0         NaN  03-Apr-21     USA    PA   
 ..         ...     ...         ...        ...     ...   ...   
 160        NaN     NaN         NaN        NaN     NaN   NaN   
 161        NaN     NaN         NaN        NaN     NaN   NaN   
 162        NaN     NaN         NaN        NaN     NaN   NaN   
 163        NaN     NaN         NaN        NaN     NaN   NaN   
 164        NaN     NaN         NaN        NaN     NaN   NaN   
 
                                            Description  Deaths Tesla driver  \
 0    Collisions with cement barrier, car catches on...     1.0            -   
 1             Tesla crashes into tree with "no driver"     2.0       

In [6]:
tesla_table = tesla_table_read[0]
tesla_table

Unnamed: 0    Year  Unnamed: 2       Date Country State  \
0          NaN  2021.0         NaN  17-Apr-21   China   NaN   
1          NaN  2021.0         NaN  17-Apr-21     USA    TX   
2          NaN  2021.0         NaN  16-Apr-21  France   NaN   
3          NaN  2021.0         NaN  14-Apr-21     USA    TX   
4          NaN  2021.0         NaN  03-Apr-21     USA    PA   
..         ...     ...         ...        ...     ...   ...   
160        NaN     NaN         NaN        NaN     NaN   NaN   
161        NaN     NaN         NaN        NaN     NaN   NaN   
162        NaN     NaN         NaN        NaN     NaN   NaN   
163        NaN     NaN         NaN        NaN     NaN   NaN   
164        NaN     NaN         NaN        NaN     NaN   NaN   

                                           Description  Deaths Tesla driver  \
0    Collisions with cement barrier, car catches on...     1.0            -   
1             Tesla crashes into tree with "no driver"     2.0          NaN   
2             Tesla crashes into tree with 5 occupants     2.0          NaN   
3                         Head-on collision with Tesla     1.0            1   
4    Tesla loses control, hits railing and cut in half     2.0            1   
..                                                 ...     ...          ...   
160                                                NaN     NaN          NaN   
161                                                NaN  2013.0         2014   
162                                                NaN     3.0            6   
163                                                NaN     NaN          NaN   
164              Note: Autopilot released Oct 14, 2015     NaN          NaN   

    Tesla occupant  ... Model Autopilot claimed Verified TeslaAutopilot Death  \
0                1  ...   NaN                 -                             -   
1              NaN  ...     S                 2                             -   
2              NaN  ...   NaN                 -                             -   
3              NaN  ...   NaN                 -                             -   
4                1  ...   NaN                 -                             -   
..             ...  ...   ...               ...                           ...   
160            NaN  ...   NaN               NaN                           NaN   
161           2015  ...  2019              2020                          2021   
162              5  ...    50                43                            23   
163            NaN  ...   NaN               NaN                           NaN   
164            NaN  ...   NaN               NaN                           NaN   

                                                Source FARS-NHTSA case filing  \
0    https://www.globaltimes.cn/page/202104/1221662...                    NaN   
1    https://www.foxbusiness.com/lifestyle/two-kill...                    NaN   
2    https://www.leprogres.fr/faits-divers-justice/...                    NaN   
3    https://www.statesman.com/story/news/2021/04/2...                    NaN   
4    https://www.citizensvoice.com/news/crime-emerg...                    NaN   
..                                                 ...                    ...   
160                                                NaN                    NaN   
161                                                NaN                    NaN   
162                                                NaN                    NaN   
163                                                NaN                    NaN   
164                                                NaN                    NaN   

              Note         Deceased 1 Deceased 2 Deceased 3 Deceased 4  
0              NaN                NaN        NaN        NaN        NaN  
1              NaN                NaN        NaN        NaN        NaN  
2              NaN                NaN        NaN        NaN        NaN  
3              NaN      Arlen Jameson        NaN        NaN 

In [7]:
tesla_table = tesla_table.drop(columns=['Unnamed: 0','Unnamed: 2', 'Date', 'State', 'Tesla driver', 'Tesla occupant','Other vehicle', 'Cyclists/ Peds', 'Model', 'Autopilot claimed', 'Verified TeslaAutopilot Death', 'Source', 'FARS-NHTSA case filing', 'Note', 'Deceased 1', 'Deceased 2', 'Deceased 3', 'Deceased 4', 'TSLA + cycl/peds'])
tesla_table = tesla_table.dropna(subset=['Year'])
tesla_table

Year Country                                        Description  Deaths
0    2021.0   China  Collisions with cement barrier, car catches on...     1.0
1    2021.0     USA           Tesla crashes into tree with "no driver"     2.0
2    2021.0  France           Tesla crashes into tree with 5 occupants     2.0
3    2021.0     USA                       Head-on collision with Tesla     1.0
4    2021.0     USA  Tesla loses control, hits railing and cut in half     2.0
..      ...     ...                                                ...     ...
150  2014.0     USA                           Tesla kills motorcyclist     1.0
151  2014.0     USA                         Thief crashes stolen Tesla     1.0
152  2014.0     USA                        Tesla rear ends stopped car     3.0
153  2013.0     USA                                Tesla kills cyclist     1.0
154  2013.0     USA                     Tesla veers into opposite lane     2.0

[155 rows x 4 columns]

In [8]:
cols = ['Year', 'Deaths']
tesla_table[cols] = tesla_table[cols].applymap(np.int64)
tesla_table['Country'] = tesla_table['Country'].replace (['FR'], 'France')
tesla_table['Country'] = tesla_table['Country'].replace (['Holland'], 'Netherlands')
tesla_table

Year Country                                        Description  Deaths
0    2021   China  Collisions with cement barrier, car catches on...       1
1    2021     USA           Tesla crashes into tree with "no driver"       2
2    2021  France           Tesla crashes into tree with 5 occupants       2
3    2021     USA                       Head-on collision with Tesla       1
4    2021     USA  Tesla loses control, hits railing and cut in half       2
..    ...     ...                                                ...     ...
150  2014     USA                           Tesla kills motorcyclist       1
151  2014     USA                         Thief crashes stolen Tesla       1
152  2014     USA                        Tesla rear ends stopped car       3
153  2013     USA                                Tesla kills cyclist       1
154  2013     USA                     Tesla veers into opposite lane       2

[155 rows x 4 columns]

In [9]:
details = pd.read_csv("static/data/tesla_deaths_details.csv")
details

Year Country  ByTeslaCount  ByOtherPartyCount  ByUndeterminedCount  \
0    2021   China             1                  0                    0   
1    2021     USA             1                  0                    0   
2    2021  France             1                  0                    0   
3    2021     USA             0                  1                    0   
4    2021     USA             1                  0                    0   
..    ...     ...           ...                ...                  ...   
150  2014     USA             1                  0                    0   
151  2014     USA             1                  0                    0   
152  2014     USA             1                  0                    0   
153  2013     USA             1                  0                    0   
154  2013     USA             1                  0                    0   

     ByInanimateObjectCount  PedestrianInvolvedCount  MotorcycleInvolvedCount  \
0                         0                        0                        0   
1                         0                        0                        0   
2                         0                        0                        0   
3                         0                        0                        0   
4                         0                        0                        0   
..                      ...                      ...                      ...   
150                       0                        0                        1   
151                       0                        0                        0   
152                       0                        0                        0   
153                       0                        1                        0   
154                       0                        0                        0   

     AutoPilotOnCount  
0                   0  
1                   0  
2                   0  
3                   0  
4                   0  
..                ...  
150                 0  
151                 0  
152                 0  
153                 0  
154                 0  

[155 rows x 9 columns]

In [10]:
tesla_table = pd.merge(tesla_table, details, on="Year")
tesla_table = tesla_table.drop(columns = ['Country_y'])
tesla_table = tesla_table.rename(columns={'Country_x':'Country'})
tesla_table

Year Country                                        Description  Deaths  \
0     2021   China  Collisions with cement barrier, car catches on...       1   
1     2021   China  Collisions with cement barrier, car catches on...       1   
2     2021   China  Collisions with cement barrier, car catches on...       1   
3     2021   China  Collisions with cement barrier, car catches on...       1   
4     2021   China  Collisions with cement barrier, car catches on...       1   
...    ...     ...                                                ...     ...   
4526  2014     USA                        Tesla rear ends stopped car       3   
4527  2013     USA                                Tesla kills cyclist       1   
4528  2013     USA                                Tesla kills cyclist       1   
4529  2013     USA                     Tesla veers into opposite lane       2   
4530  2013     USA                     Tesla veers into opposite lane       2   

      ByTeslaCount  ByOtherPartyCount  ByUndeterminedCount  \
0                1                  0                    0   
1                1                  0                    0   
2                1                  0                    0   
3                0                  1                    0   
4                1                  0                    0   
...            ...                ...                  ...   
4526             1                  0                    0   
4527             1                  0                    0   
4528             1                  0                    0   
4529             1                  0                    0   
4530             1                  0                    0   

      ByInanimateObjectCount  PedestrianInvolvedCount  \
0                          0                        0   
1                          0                        0   
2                          0                        0   
3                          0                        0   
4                          0                        0   
...                      ...                      ...   
4526                       0                        0   
4527                       0                        1   
4528                       0                        0   
4529                       0                        1   
4530                       0                        0   

      MotorcycleInvolvedCount  AutoPilotOnCount  
0                           0                 0  
1                           0                 0  
2                           0                 0  
3                           0                 0  
4                           0                 0  
...                       ...               ...  
4526                        0                 0  
4527                        0                 0  
4528                        0                 0  
4529                        0                 0  
4530                        0                 0  

[4531 rows x 11 columns]

In [11]:
# Turning to CSV
tesla_table.to_csv('static/data/tesla_deaths_scraped.csv', index = False)

In [12]:
# Turning to JSON
result = tesla_table.to_json(orient="records")
parsed = json.loads(result)
print(json.dumps(parsed, indent=4, sort_keys=True))

[
    {
        "AutoPilotOnCount": 0,
        "ByInanimateObjectCount": 0,
        "ByOtherPartyCount": 0,
        "ByTeslaCount": 1,
        "ByUndeterminedCount": 0,
        "Country": "China",
        "Deaths": 1,
        "Description": "Collisions with cement barrier, car catches on fire",
        "MotorcycleInvolvedCount": 0,
        "PedestrianInvolvedCount": 0,
        "Year": 2021
    },
    {
        "AutoPilotOnCount": 0,
        "ByInanimateObjectCount": 0,
        "ByOtherPartyCount": 0,
        "ByTeslaCount": 1,
        "ByUndeterminedCount": 0,
        "Country": "China",
        "Deaths": 1,
        "Description": "Collisions with cement barrier, car catches on fire",
        "MotorcycleInvolvedCount": 0,
        "PedestrianInvolvedCount": 0,
        "Year": 2021
    },
    {
        "AutoPilotOnCount": 0,
        "ByInanimateObjectCount": 0,
        "ByOtherPartyCount": 0,
        "ByTeslaCount": 1,
        "ByUndeterminedCount": 0,
        "Country": "China",
       

In [13]:
with open("static/data/tesla_deaths_scraped.json", "w") as outfile:
    json.dump(parsed, outfile)

In [14]:
conn = 'mongodb://localhost:27017'
client = pymongo.MongoClient(conn)

db = client.project3

In [15]:
db.tesla_deaths

Collection(Database(MongoClient(host=['localhost:27017'], document_class=dict, tz_aware=False, connect=True), 'project3'), 'tesla_deaths')

In [16]:
# Query all students
# Here, db.students refers to the collection 'classroom '
# tesla_deaths = db.tesla_deaths.find()

# Select database and collection to use
db = client.project3
db = client.project3
tesla_deaths =db.tesla_deaths
tesla_deaths.insert_many(parsed)

In [17]:
# Query all students
# Here, db.students refers to the collection 'classroom '
tesla_deaths = db.tesla_deaths.find()

# Iterate through each student in the collection
for i in tesla_deaths:
    print(i)

{'_id': ObjectId('6088984a9ce930dde73a08fc'), 'Year': 2021, 'Country': 'China', 'Description': 'Collisions with cement barrier, car catches on fire', 'Deaths': 1}
{'_id': ObjectId('6088984a9ce930dde73a08fd'), 'Year': 2021, 'Country': 'USA', 'Description': 'Tesla crashes into tree with "no driver"', 'Deaths': 2}
{'_id': ObjectId('6088984a9ce930dde73a08fe'), 'Year': 2021, 'Country': 'France', 'Description': 'Tesla crashes into tree with 5 occupants', 'Deaths': 2}
{'_id': ObjectId('6088984a9ce930dde73a08ff'), 'Year': 2021, 'Country': 'USA', 'Description': 'Head-on collision with Tesla', 'Deaths': 1}
{'_id': ObjectId('6088984a9ce930dde73a0900'), 'Year': 2021, 'Country': 'USA', 'Description': 'Tesla loses control, hits railing and cut in half', 'Deaths': 2}
{'_id': ObjectId('6088984a9ce930dde73a0901'), 'Year': 2021, 'Country': 'UK', 'Description': 'Pedestrian hit in collision, later dies in hospital weeks later', 'Deaths': 1}
{'_id': ObjectId('6088984a9ce930dde73a0902'), 'Year': 2021, 'Coun

{'_id': ObjectId('6089dbee256a4e3b68b0d177'), 'Year': 2020, 'Country': 'Norway', 'Description': 'Tesla strikes a man standing next to his parked truck', 'Deaths': 1, 'ByTeslaCount': 'no', 'ByOtherPartyCount': 'no', 'ByUndeterminedCount': 'yes', 'ByInanimateObjectCount': 'no', 'PedestrianInvolvedCount': 'no', 'MotorcycleInvolvedCount': 'no', 'AutoPilotOnCount': 'no'}
{'_id': ObjectId('6089dbee256a4e3b68b0d178'), 'Year': 2020, 'Country': 'Norway', 'Description': 'Tesla strikes a man standing next to his parked truck', 'Deaths': 1, 'ByTeslaCount': 'yes', 'ByOtherPartyCount': 'no', 'ByUndeterminedCount': 'no', 'ByInanimateObjectCount': 'no', 'PedestrianInvolvedCount': 'no', 'MotorcycleInvolvedCount': 'no', 'AutoPilotOnCount': 'no'}
{'_id': ObjectId('6089dbee256a4e3b68b0d179'), 'Year': 2020, 'Country': 'Norway', 'Description': 'Tesla strikes a man standing next to his parked truck', 'Deaths': 1, 'ByTeslaCount': 'no', 'ByOtherPartyCount': 'yes', 'ByUndeterminedCount': 'no', 'ByInanimateObjec

{'_id': ObjectId('6089dbee256a4e3b68b0d946'), 'Year': 2019, 'Country': 'USA', 'Description': "Car drifts into Tesla's lane", 'Deaths': 1, 'ByTeslaCount': 'no', 'ByOtherPartyCount': 'yes', 'ByUndeterminedCount': 'no', 'ByInanimateObjectCount': 'no', 'PedestrianInvolvedCount': 'no', 'MotorcycleInvolvedCount': 'no', 'AutoPilotOnCount': 'no'}
{'_id': ObjectId('6089dbee256a4e3b68b0d947'), 'Year': 2019, 'Country': 'USA', 'Description': "Car drifts into Tesla's lane", 'Deaths': 1, 'ByTeslaCount': 'yes', 'ByOtherPartyCount': 'no', 'ByUndeterminedCount': 'no', 'ByInanimateObjectCount': 'no', 'PedestrianInvolvedCount': 'yes', 'MotorcycleInvolvedCount': 'no', 'AutoPilotOnCount': 'no'}
{'_id': ObjectId('6089dbee256a4e3b68b0d948'), 'Year': 2019, 'Country': 'USA', 'Description': "Car drifts into Tesla's lane", 'Deaths': 1, 'ByTeslaCount': 'yes', 'ByOtherPartyCount': 'no', 'ByUndeterminedCount': 'no', 'ByInanimateObjectCount': 'no', 'PedestrianInvolvedCount': 'no', 'MotorcycleInvolvedCount': 'no', 'A

{'_id': ObjectId('6089e039a02dc11e0a3e3a82'), 'Year': 2020, 'Country': 'USA', 'Description': 'Tesla runs thru red light, crashes, driver dies at scene', 'Deaths': 1, 'ByTeslaCount': 'no', 'ByOtherPartyCount': 'no', 'ByUndeterminedCount': 'yes', 'ByInanimateObjectCount': 'no', 'PedestrianInvolvedCount': 'no', 'MotorcycleInvolvedCount': 'no', 'AutoPilotOnCount': 'no'}
{'_id': ObjectId('6089e039a02dc11e0a3e3a83'), 'Year': 2020, 'Country': 'USA', 'Description': 'Tesla runs thru red light, crashes, driver dies at scene', 'Deaths': 1, 'ByTeslaCount': 'yes', 'ByOtherPartyCount': 'no', 'ByUndeterminedCount': 'no', 'ByInanimateObjectCount': 'no', 'PedestrianInvolvedCount': 'no', 'MotorcycleInvolvedCount': 'no', 'AutoPilotOnCount': 'no'}
{'_id': ObjectId('6089e039a02dc11e0a3e3a84'), 'Year': 2020, 'Country': 'USA', 'Description': 'Tesla runs thru red light, crashes, driver dies at scene', 'Deaths': 1, 'ByTeslaCount': 'no', 'ByOtherPartyCount': 'yes', 'ByUndeterminedCount': 'no', 'ByInanimateObjec

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [18]:
# this is what will go in the scrape.py file

# url = 'https://www.tesladeaths.com/'
# tesla_table = pd.read_html(url)
# tesla_table = tesla_table[0]
# tesla_table = tesla_table.drop(columns=['Unnamed: 0','Unnamed: 2', 'Date', 'State', 'Tesla driver', 'Tesla occupant','Other vehicle', 'Cyclists/ Peds', 'Model', 'Autopilot claimed', 'Verified TeslaAutopilot Death', 'Source', 'FARS-NHTSA case filing', 'Note', 'Deceased 1', 'Deceased 2', 'Deceased 3', 'Deceased 4', 'TSLA + cycl/peds'])
# tesla_table = tesla_table.dropna(subset=['Year'])
# cols = ['Year', 'Deaths']
# tesla_table[cols] = tesla_table[cols].applymap(np.int64)
# tesla_table['Country'] = tesla_table['Country'].replace (['FR'], 'France')
# tesla_table['Country'] = tesla_table['Country'].replace (['Holland'], 'Netherlands')
# details = pd.read_csv("static/data/tesla_deaths_details.csv")
# tesla_table = pd.merge(tesla_table, details, on="Year")
# tesla_table = tesla_table.drop(columns = ['Country_y'])
# tesla_table = tesla_table.rename(columns={'Country_x':'Country'})
# result = tesla_table.to_json(orient="records")
# parsed = json.loads(result)